# Выбор локации для скважины

Допустим, вы работаете в добывающей компании «ГлавРосГосНефть». Нужно решить, где бурить новую скважину.

Вам предоставлены пробы нефти в трёх регионах: в каждом 10 000 месторождений, где измерили качество нефти и объём её запасов. Постройте модель машинного обучения, которая поможет определить регион, где добыча принесёт наибольшую прибыль. Проанализируйте возможную прибыль и риски техникой *Bootstrap.*

Шаги для выбора локации:

- В избранном регионе ищут месторождения, для каждого определяют значения признаков;
- Строят модель и оценивают объём запасов;
- Выбирают месторождения с самым высокими оценками значений. Количество месторождений зависит от бюджета компании и стоимости разработки одной скважины;
- Прибыль равна суммарной прибыли отобранных месторождений.

## Загрузка и подготовка данных

In [5]:
import pandas as pd
import pandas_profiling
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
from scipy import stats as st

from pathlib import Path

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import KFold
from sklearn.utils import shuffle

In [6]:
REG_BUDGET = 10_000_000_000 #бюджет разработкы скважин в регионе
VALUE_BARREL = 450_000 #стоимость барреля нефти
N_EST = 500 #количество измерений в одном регионе
N_HOLES = 200 #количество скважин с лучшими показателями 

In [7]:
def find_and_select_data_files(data_sources, assign_to=None):
    data_frames = {}

    for variable, paths in data_sources.items():
        for file_path in paths:
            file = Path(file_path)
            if file.exists() and file.is_file():
                try:
                    supported_formats = ['.csv', '.xls', '.xlsx']
                    if file.suffix in supported_formats:
                        df = pd.read_excel(file) if file.suffix in ['.xls', '.xlsx'] else pd.read_csv(file)
                        data_frames[variable] = df
                        print(f"Для переменной '{variable}' прочитан файл: {file}")
                        if assign_to is not None and variable in assign_to:
                            globals()[assign_to[variable]] = df
                    else:
                        print(f"Формат файла '{file.suffix}' не поддерживается.")
                except Exception as e:
                    print(f"Ошибка при чтении файла '{file}': {e}")
                break
        else:
            print(f"Файл данных для переменной '{variable}' не найден.")
    
    return data_frames

In [8]:
data_sources = {
    "df0": ['/datasets/geo_data_0.csv', 'geo_data_0.csv'],
    "df1": ['/datasets/geo_data_1.csv', 'geo_data_1.csv'],
    "df2": ['/datasets/geo_data_2.csv', 'geo_data_2.csv']
}

assignments = {
    "df0": "df0",
    "df1": "df1",
    "df2": "df2"
}


dfs = find_and_select_data_files(data_sources, assign_to=assignments)

Для переменной 'df0' прочитан файл: geo_data_0.csv
Для переменной 'df1' прочитан файл: geo_data_1.csv
Для переменной 'df2' прочитан файл: geo_data_2.csv


In [9]:
df0.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [10]:
df1.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [11]:
df2.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Вот что мы имеем:
* Нам совершенно не понадобится столбец id для целей работы - не важно как называтся объект составляющий совокупность для оценки. Будем удалять
* Во всех регионах наблюдается сильная корреляция признака f2 с таргетом, но во втором регионе (df1) она близка к единице. Во первых, очевидно, что этот признак наиболее важный показатель для объемов месторождений, а, во-вторых, скорее всего модель будет наиболее предсказуемой и качественной именно на данныйх второго региона
* Стоит сделать масштабирование признаков - у них явно разные порядки
* Данные чистые, пустых значений нет, объемов вполне достаточно для наших целей. 


In [12]:
df0 = df0.drop(['id'], axis=1)
df1 = df1.drop(['id'], axis=1)
df2 = df2.drop(['id'], axis=1)

Для масштабирования признаков будем использовать функцию:

In [13]:
def scaler(features):
    num_df = features.loc[:, ['f0', 'f1', 'f2']]

    scaler = StandardScaler()
    scaler_df = pd.DataFrame(data=scaler.fit_transform(num_df), index=features.index, columns=num_df.columns) 
    scaler_df = pd.concat(
        (
            scaler_df, features.drop(
                ['f0', 'f1', 'f2'], axis=1
            )
        ), axis=1
    )
    return scaler_df

## Обучение и проверка модели

Напишем функцию для разделения выборок:

In [14]:
def splitter(data, part='all'):
    features = data.drop(['product'], axis=1) 
    target = data['product']

    features_train, features_valid, target_train, target_valid = \
    train_test_split(features, target, test_size=0.25, random_state=12345)
    
    features_train = scaler(features_train)
    features_valid = scaler(features_valid)
         
    if part == 'train':
        return features_train, target_train
    elif part == 'valid':
        return features_valid, target_valid
    elif part == 'all':
        return features_train, target_train, features_valid, target_valid

Функция folder отвечает за проверку модели на нескольких выборках, полученных с помощью kfold, а на выходе выдает лучший RMSE, средний RMSE по всем выборкам и среднее значение предсказанной величины(объема добычи)

In [15]:
def folder(data):    
    features = data.drop(['product'], axis=1) 
    target = data['product']

    kfold = KFold(n_splits=5, random_state=123456, shuffle=True)

    best_result = 100

    for train_index, test_index in kfold.split(features):
        features_train, features_test = features.loc[train_index], features.loc[test_index]
        target_train, target_test = target.loc[train_index], target.loc[test_index]
        best_model = None
        features_train = scaler(features_train)
        features_test = scaler(features_test)

        rmse = []

        model = LinearRegression() 
        model.fit(features_train, target_train) 
        predicted = model.predict(features_test)
        result = mean_squared_error(target_test, predicted, squared=False) 

        if result < best_result:
            best_result = result
        rmse.append(result)
    return best_result, np.mean(rmse),  predicted.mean() 

Пройдем с этой функцией циколм по всем регионам:

In [16]:
i = 0
for region in [df0, df1, df2]:
    
    i += 1
    
    print (
        'Для', i, 'региона:\n',
        'Лучший RMSE:', folder(region)[0], '\n',
        'Cредняя RMSE для всех выборок:', folder(region)[1], '\n',
        'Cредний объем предсказанного сырья:', folder(region)[2], '\n',
    )

Для 1 региона:
 Лучший RMSE: 37.60633908678906 
 Cредняя RMSE для всех выборок: 37.60633908678906 
 Cредний объем предсказанного сырья: 92.51008592683276 

Для 2 региона:
 Лучший RMSE: 0.9031251761903286 
 Cредняя RMSE для всех выборок: 0.9833642056454017 
 Cредний объем предсказанного сырья: 68.90017022613456 

Для 3 региона:
 Лучший RMSE: 39.85256666435327 
 Cредняя RMSE для всех выборок: 39.97839065918039 
 Cредний объем предсказанного сырья: 94.88965712515007 



* Во-первых среднее значение и лучшее для rmse в каждом из регионов сравнимы друг с другом - модель работает адекватно. 
* Интересен, также факт заметно низкой rmse во втором регионе - почти 1 в среднем по всем выборкам. Это подтверждает догадку о корреляции признака с таргетом. 
* При всём качестве модели для второго региона, объем предсказанного сырья здесь ниже всех. Выводы делать рано, так как rmse 38 и 40 для 1 и 3 регионов, соответственно, вполне дает пространство как для более высоких значений среднего объема, так и для более низких у этих регионов. 


Используем проверенную модель и обучим ее с помошью заготовленной функции для каждого региона:

In [17]:
def predictor(data):
    features_train, target_train, features_valid, target_valid = \
    splitter(data, part='all')
    features_train = scaler(features_train)
    features_valid = scaler(features_valid)
    
    model = LinearRegression() 
    model.fit(features_train, target_train)
    predict_valid = model.predict(features_valid)
    
    return target_valid.reset_index(drop=True), predict_valid
    

In [18]:
target_valid_0, predict_valid_0 = predictor(df0)
target_valid_1, predict_valid_1 = predictor(df1)
target_valid_2, predict_valid_2 = predictor(df2)

## Подготовка к расчёту прибыли

Посчитаем, стоимость строительства одной вышки и какое количество нефти окупит ее существование

In [19]:
hole_cost = REG_BUDGET / N_HOLES
benefit_hole_raw = hole_cost / VALUE_BARREL


In [20]:
print (
        'Бюджет разработки одной скважины:', hole_cost, '\n',
        'Для безубыточной работы скважины потребуется объем в:', benefit_hole_raw, ' ,тыс баррелей \n'
    )

Бюджет разработки одной скважины: 50000000.0 
 Для безубыточной работы скважины потребуется объем в: 111.11111111111111  ,тыс баррелей 



Средний запас скважин:

In [21]:
i = 0
for region in [df0, df1, df2]:
    i += 1
    print (
        'Для', i, 'региона:\n',
        'средний запас сырья:', region['product'].mean()
    )

Для 1 региона:
 средний запас сырья: 92.50000000000001
Для 2 региона:
 средний запас сырья: 68.82500000000002
Для 3 региона:
 средний запас сырья: 95.00000000000004


Полученные средние запасы ниже чем необходимый объем нефти, для безубыточной работы скважины. Особенно низкий объем во втором регионе - всего 69 тыс баррелей из необходимых 111. 

## Расчёт прибыли и рисков 

Напишем функцию для выбора лучших измерений, отдающую на выходе суммарную прибыль из указанного выбранного количества измерений.

In [22]:
def revenue(target, probabilities, count):
    probs_sorted = probabilities.sort_values(ascending=False)
    selected = target[probs_sorted.index][:count]
    return VALUE_BARREL * selected.sum() - REG_BUDGET

Функцию используем при бутстрэпе с 1000 разделений и найдем доверительные итервалы, определив риски убытков для каждог региона. 

In [23]:
bootstrap_keys = np.array(
    (
        [target_valid_0, predict_valid_0], 
        [target_valid_1, predict_valid_1],
        [target_valid_2, predict_valid_2],
    )
)

In [24]:
state = np.random.RandomState(12345)

i = 0

for region in bootstrap_keys[(0,1,2),]:

    i += 1
    probabilities = pd.Series(region[1])
    values = []
    
    for j in range(1000):
        target_subsample = pd.Series(region[0]).sample(N_EST, replace=True, random_state=state)
        probs_subsample = probabilities[target_subsample.index] 
        values.append(revenue(target_subsample, probs_subsample, N_HOLES))
           
    values = pd.Series(values)
    lower = values.quantile(0.025)
    upper = values.quantile(0.975)
    mean = values.mean()
    
    print (
        'Для', i, 'региона:\n', 
        "Средняя выручка:", round(mean/1000000000, 2), 'млрд\n',
        "2.5%-квантиль:", round(lower/1000000000, 2), 'млрд\n',
        "97.5%-квантиль:", round(upper/1000000000,2), 'млрд\n',
        "разброс", round((mean - lower)/1000000000, 2), 'млрд\n'
        "Риск убытков = {:.2%}\n".format((pd.Series(values)<0).mean())
    )

Для 1 региона:
 Средняя выручка: 0.43 млрд
 2.5%-квантиль: -0.1 млрд
 97.5%-квантиль: 0.95 млрд
 разброс 0.53 млрд
Риск убытков = 6.10%

Для 2 региона:
 Средняя выручка: 0.52 млрд
 2.5%-квантиль: 0.13 млрд
 97.5%-квантиль: 0.95 млрд
 разброс 0.39 млрд
Риск убытков = 0.30%

Для 3 региона:
 Средняя выручка: 0.42 млрд
 2.5%-квантиль: -0.12 млрд
 97.5%-квантиль: 0.99 млрд
 разброс 0.54 млрд
Риск убытков = 6.20%



Не смотря на низкие показатели средней выручки и объемов добычи при обучении модели, второй регион показывает лучий результат при оценке рисков:
* 2,5% квантиль только во вторм регионе превышает нулевой порог, причем на 15 миллионов
* При этом оценка дает здесь наивысший показатель средней выручки с наименьшей дисперсией
* Также риск убытков у регина под номером два всего 0,3% в сравнении с 6% у 1 и 3 претендентов

Для разработки выбираем второй регион (geo_data_1.csv)